<div class="alert alert-primary" style="margin-top: 20px">


<h1><center>Hybrid Recommender System</center></h1>

</div>

![Açıklama](https://www.alpha-quantum.com/blog/wp-content/uploads/2020/05/img_5ecd84900a885.png)

---

### Use item-based and user-based recommender methods to make predictions for the user with the given ID.
### Take 5 recommendations from the user-based model and 5 recommendations from the item-based model, and finally, make 10 recommendations from the 2 models.


---
# Task 1: Preparing the Data
___

### Step 1: Read the Movie and Rating datasets.

In [1]:
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"
import pandas as pd
pd.set_option("display.width", 1000)
pd.set_option("display.max_columns", None)
pd.set_option("display.expand_frame_repr", False)

df_movie = pd.read_csv("/kaggle/input/movie-and-rating/movie.csv")
df_rating = pd.read_csv("/kaggle/input/movie-and-rating/rating.csv")
df_movie.head()
df_rating.head()

df_movie.shape
df_rating.shape
df_rating["movieId"].nunique()
df_movie["movieId"].nunique()
df_movie.isnull().sum()
df_rating.isnull().sum()


userId       0
movieId      0
rating       0
timestamp    0
dtype: int64

###  Step 2: Add movie names and genres to the Rating dataset using the Movie dataset.

In [2]:
df = df_rating.merge(df_movie)
df.head()

userId  movieId  rating            timestamp                                              title                                  genres
0       1        2     3.5  2005-04-02 23:53:47                                     Jumanji (1995)              Adventure|Children|Fantasy
1       1       29     3.5  2005-04-02 23:31:16  City of Lost Children, The (Cité des enfants p...  Adventure|Drama|Fantasy|Mystery|Sci-Fi
2       1       32     3.5  2005-04-02 23:33:39          Twelve Monkeys (a.k.a. 12 Monkeys) (1995)                 Mystery|Sci-Fi|Thriller
3       1       47     3.5  2005-04-02 23:32:07                        Seven (a.k.a. Se7en) (1995)                        Mystery|Thriller
4       1       50     3.5  2005-04-02 23:29:40                         Usual Suspects, The (1995)                  Crime|Mystery|Thriller

### Step 3: Calculate the total number of people who rated each movie. Remove movies with less than 1000 ratings from the dataset.

In [3]:
df["title"].value_counts().head()

comment_counts = pd.DataFrame(df["title"].value_counts())

df.shape

rare_movies = comment_counts[comment_counts["count"] <= 1000].index
rare_movies.shape

common_movies = df[~df["title"].isin(rare_movies)]
common_movies.shape

title
Pulp Fiction (1994)                 67310
Forrest Gump (1994)                 66172
Shawshank Redemption, The (1994)    63366
Silence of the Lambs, The (1991)    63299
Jurassic Park (1993)                59715
Name: count, dtype: int64

(20000263, 6)

(23570,)

(17766015, 6)

### Step 4: Create a pivot table where the index is userId, columns are movie names, and the values are ratings.


In [4]:
user_movie_df = common_movies.pivot_table(index="userId",
                                          columns="title",
                                          values="rating")
user_movie_df.head()

title   'burbs, The (1989)  (500) Days of Summer (2009)  *batteries not included (1987)  ...And Justice for All (1979)  10 Things I Hate About You (1999)  10,000 BC (2008)  101 Dalmatians (1996)  101 Dalmatians (One Hundred and One Dalmatians) (1961)  102 Dalmatians (2000)  12 Angry Men (1957)  12 Years a Slave (2013)  127 Hours (2010)  13 Going on 30 (2004)  13th Warrior, The (1999)  1408 (2007)  15 Minutes (2001)  16 Blocks (2006)  17 Again (2009)  1984 (Nineteen Eighty-Four) (1984)  2 Days in the Valley (1996)  2 Fast 2 Furious (Fast and the Furious 2, The) (2003)  20,000 Leagues Under the Sea (1954)  200 Cigarettes (1999)  2001: A Space Odyssey (1968)  2010: The Year We Make Contact (1984)  2012 (2009)  2046 (2004)  21 (2008)  21 Grams (2003)  21 Jump Street (2012)  24 Hour Party People (2002)  25th Hour (2002)  27 Dresses (2008)  28 Days (2000)  28 Days Later (2002)  28 Weeks Later (2007)  3 Ninjas (1992)  3-Iron (Bin-jip) (2004)  30 Days of Night (2007)  300 (2007)  3000 Miles to Graceland (2001)  39 Steps, The (1935)  3:10 to Yuma (2007)  40 Days and 40 Nights (2002)  40-Year-Old Virgin, The (2005)  400 Blows, The (Les quatre cents coups) (1959)  42 Up (1998)  48 Hrs. (1982)  50 First Dates (2004)  50/50 (2011)  54 (1998)  6th Day, The (2000)  7th Voyage of Sinbad, The (1958)  8 1/2 (8½) (1963)  8 Heads in a Duffel Bag (1997)  8 Mile (2002)  8MM (1999)  9 (2009)  9 1/2 Weeks (Nine 1/2 Weeks) (1986)  A-Team, The (2010)  A.I. Artificial Intelligence (2001)  AVP: Alien vs. Predator (2004)  AVPR: Aliens vs. Predator - Requiem (2007)  About Last Night... (1986)  About Schmidt (2002)  About a Boy (2002)  Absent-Minded Professor, The (1961)  Absolute Power (1997)  Abyss, The (1989)  Accepted (2006)  Accidental Tourist, The (1988)  Accused, The (1988)  Ace Ventura: Pet Detective (1994)  Ace Ventura: When Nature Calls (1995)  Across the Universe (2007)  Adaptation (2002)  Addams Family Values (1993)  Addams Family, The (1991)  Addicted to Love (1997)  Adjustment Bureau, The (2011)  Adventureland (2009)  Adventures in Babysitting (1987)  Adventures of Baron Munchausen, The (1988)  Adventures of Buckaroo Banzai Across the 8th Dimension, The (1984)  Adventures of Milo and Otis, The (Koneko monogatari) (1986)  Adventures of Pinocchio, The (1996)  Adventures of Priscilla, Queen of the Desert, The (1994)  Adventures of Robin Hood, The (1938)  Adventures of Rocky and Bullwinkle, The (2000)  Adventures of Tintin, The (2011)  Aeon Flux (2005)  Affair to Remember, An (1957)  Affliction (1997)  African Queen, The (1951)  After Hours (1985)  Age of Innocence, The (1993)  Agnes of God (1985)  Aguirre: The Wrath of God (Aguirre, der Zorn Gottes) (1972)  Air America (1990)  Air Bud (1997)  Air Force One (1997)  Airheads (1994)  Airplane II: The Sequel (1982)  Airplane! (1980)  Airport (1970)  Akira (1988)  Aladdin (1992)  Aladdin and the King of Thieves (1996)  Alexander (2004)  Alfie (2004)  Ali (2001)  Alice in Wonderland (1951)  Alice in Wonderland (2010)  Alien (1979)  Alien Nation (1988)  Alien: Resurrection (1997)  Aliens (1986)  Alien³ (a.k.a. Alien 3) (1992)  Alive (1993)  All About Eve (1950)  All About My Mother (Todo sobre mi madre) (1999)  All Dogs Go to Heaven (1989)  All Dogs Go to Heaven 2 (1996)  All Quiet on the Western Front (1930)  All That Jazz (1979)  All the President's Men (1976)  All the Pretty Horses (2000)  Almost Famous (2000)  Along Came Polly (2004)  Along Came a Spider (2001)  Alphaville (Alphaville, une étrange aventure de Lemmy Caution) (1965)  Altered States (1980)  Always (1989)  Amadeus (1984)  Amateur (1994)  Amazing Spider-Man, The (2012)  Amelie (Fabuleux destin d'Amélie Poulain, Le) (2001)  America's Sweethearts (2001)  American Beauty (1999)  American Gangster (2007)  American Gigolo (1980)  American Graffiti (1973)  American History X (1998)  American Hustle (2013)  American Movie (1999)  American Pie (1999)  American Pie 2 (2001)  American President, The (1995)  American Psycho (2000)  American Splendo

### Step 5: Turn all the above steps into a function.

In [5]:
def create_user_movie_df(df):
    df = df_movie.merge(df_rating)
    comment_counts = pd.DataFrame(df["title"].value_counts())
    rare_movies = comment_counts[comment_counts["count"] <= 1000].index
    common_movies = df[~df["title"].isin(rare_movies)]
    user_movie_df = common_movies.pivot_table(index="userId", columns="title", values="rating")
    return user_movie_df
create_user_movie_df(df)

title   'burbs, The (1989)  (500) Days of Summer (2009)  *batteries not included (1987)  ...And Justice for All (1979)  10 Things I Hate About You (1999)  10,000 BC (2008)  101 Dalmatians (1996)  101 Dalmatians (One Hundred and One Dalmatians) (1961)  102 Dalmatians (2000)  12 Angry Men (1957)  12 Years a Slave (2013)  127 Hours (2010)  13 Going on 30 (2004)  13th Warrior, The (1999)  1408 (2007)  15 Minutes (2001)  16 Blocks (2006)  17 Again (2009)  1984 (Nineteen Eighty-Four) (1984)  2 Days in the Valley (1996)  2 Fast 2 Furious (Fast and the Furious 2, The) (2003)  20,000 Leagues Under the Sea (1954)  200 Cigarettes (1999)  2001: A Space Odyssey (1968)  2010: The Year We Make Contact (1984)  2012 (2009)  2046 (2004)  21 (2008)  21 Grams (2003)  21 Jump Street (2012)  24 Hour Party People (2002)  25th Hour (2002)  27 Dresses (2008)  28 Days (2000)  28 Days Later (2002)  28 Weeks Later (2007)  3 Ninjas (1992)  3-Iron (Bin-jip) (2004)  30 Days of Night (2007)  300 (2007)  3000 Miles to Graceland (2001)  39 Steps, The (1935)  3:10 to Yuma (2007)  40 Days and 40 Nights (2002)  40-Year-Old Virgin, The (2005)  400 Blows, The (Les quatre cents coups) (1959)  42 Up (1998)  48 Hrs. (1982)  50 First Dates (2004)  50/50 (2011)  54 (1998)  6th Day, The (2000)  7th Voyage of Sinbad, The (1958)  8 1/2 (8½) (1963)  8 Heads in a Duffel Bag (1997)  8 Mile (2002)  8MM (1999)  9 (2009)  9 1/2 Weeks (Nine 1/2 Weeks) (1986)  A-Team, The (2010)  A.I. Artificial Intelligence (2001)  AVP: Alien vs. Predator (2004)  AVPR: Aliens vs. Predator - Requiem (2007)  About Last Night... (1986)  About Schmidt (2002)  About a Boy (2002)  Absent-Minded Professor, The (1961)  Absolute Power (1997)  Abyss, The (1989)  Accepted (2006)  Accidental Tourist, The (1988)  Accused, The (1988)  Ace Ventura: Pet Detective (1994)  Ace Ventura: When Nature Calls (1995)  Across the Universe (2007)  Adaptation (2002)  Addams Family Values (1993)  Addams Family, The (1991)  Addicted to Love (1997)  Adjustment Bureau, The (2011)  Adventureland (2009)  Adventures in Babysitting (1987)  Adventures of Baron Munchausen, The (1988)  Adventures of Buckaroo Banzai Across the 8th Dimension, The (1984)  Adventures of Milo and Otis, The (Koneko monogatari) (1986)  Adventures of Pinocchio, The (1996)  Adventures of Priscilla, Queen of the Desert, The (1994)  Adventures of Robin Hood, The (1938)  Adventures of Rocky and Bullwinkle, The (2000)  Adventures of Tintin, The (2011)  Aeon Flux (2005)  Affair to Remember, An (1957)  Affliction (1997)  African Queen, The (1951)  After Hours (1985)  Age of Innocence, The (1993)  Agnes of God (1985)  Aguirre: The Wrath of God (Aguirre, der Zorn Gottes) (1972)  Air America (1990)  Air Bud (1997)  Air Force One (1997)  Airheads (1994)  Airplane II: The Sequel (1982)  Airplane! (1980)  Airport (1970)  Akira (1988)  Aladdin (1992)  Aladdin and the King of Thieves (1996)  Alexander (2004)  Alfie (2004)  Ali (2001)  Alice in Wonderland (1951)  Alice in Wonderland (2010)  Alien (1979)  Alien Nation (1988)  Alien: Resurrection (1997)  Aliens (1986)  Alien³ (a.k.a. Alien 3) (1992)  Alive (1993)  All About Eve (1950)  All About My Mother (Todo sobre mi madre) (1999)  All Dogs Go to Heaven (1989)  All Dogs Go to Heaven 2 (1996)  All Quiet on the Western Front (1930)  All That Jazz (1979)  All the President's Men (1976)  All the Pretty Horses (2000)  Almost Famous (2000)  Along Came Polly (2004)  Along Came a Spider (2001)  Alphaville (Alphaville, une étrange aventure de Lemmy Caution) (1965)  Altered States (1980)  Always (1989)  Amadeus (1984)  Amateur (1994)  Amazing Spider-Man, The (2012)  Amelie (Fabuleux destin d'Amélie Poulain, Le) (2001)  America's Sweethearts (2001)  American Beauty (1999)  American Gangster (2007)  American Gigolo (1980)  American Graffiti (1973)  American History X (1998)  American Hustle (2013)  American Movie (1999)  American Pie (1999)  American Pie 2 (2001)  American President, The (1995)  American Psycho (2000)  American Splendo

---
# Task 2: Identifying the Movies Watched by the User to be Recommended
---

### Step 1: Randomly select a user id.

In [6]:
random_user = user_movie_df.index[user_movie_df.index.to_series().sample(1, random_state=45).index[0]]
random_user

28942

### Step 2: Create a new dataframe named random_user_df consisting of the observation units of the selected user.

In [7]:
random_user_df = user_movie_df[user_movie_df.index == random_user]
random_user_df.head()

title   'burbs, The (1989)  (500) Days of Summer (2009)  *batteries not included (1987)  ...And Justice for All (1979)  10 Things I Hate About You (1999)  10,000 BC (2008)  101 Dalmatians (1996)  101 Dalmatians (One Hundred and One Dalmatians) (1961)  102 Dalmatians (2000)  12 Angry Men (1957)  12 Years a Slave (2013)  127 Hours (2010)  13 Going on 30 (2004)  13th Warrior, The (1999)  1408 (2007)  15 Minutes (2001)  16 Blocks (2006)  17 Again (2009)  1984 (Nineteen Eighty-Four) (1984)  2 Days in the Valley (1996)  2 Fast 2 Furious (Fast and the Furious 2, The) (2003)  20,000 Leagues Under the Sea (1954)  200 Cigarettes (1999)  2001: A Space Odyssey (1968)  2010: The Year We Make Contact (1984)  2012 (2009)  2046 (2004)  21 (2008)  21 Grams (2003)  21 Jump Street (2012)  24 Hour Party People (2002)  25th Hour (2002)  27 Dresses (2008)  28 Days (2000)  28 Days Later (2002)  28 Weeks Later (2007)  3 Ninjas (1992)  3-Iron (Bin-jip) (2004)  30 Days of Night (2007)  300 (2007)  3000 Miles to Graceland (2001)  39 Steps, The (1935)  3:10 to Yuma (2007)  40 Days and 40 Nights (2002)  40-Year-Old Virgin, The (2005)  400 Blows, The (Les quatre cents coups) (1959)  42 Up (1998)  48 Hrs. (1982)  50 First Dates (2004)  50/50 (2011)  54 (1998)  6th Day, The (2000)  7th Voyage of Sinbad, The (1958)  8 1/2 (8½) (1963)  8 Heads in a Duffel Bag (1997)  8 Mile (2002)  8MM (1999)  9 (2009)  9 1/2 Weeks (Nine 1/2 Weeks) (1986)  A-Team, The (2010)  A.I. Artificial Intelligence (2001)  AVP: Alien vs. Predator (2004)  AVPR: Aliens vs. Predator - Requiem (2007)  About Last Night... (1986)  About Schmidt (2002)  About a Boy (2002)  Absent-Minded Professor, The (1961)  Absolute Power (1997)  Abyss, The (1989)  Accepted (2006)  Accidental Tourist, The (1988)  Accused, The (1988)  Ace Ventura: Pet Detective (1994)  Ace Ventura: When Nature Calls (1995)  Across the Universe (2007)  Adaptation (2002)  Addams Family Values (1993)  Addams Family, The (1991)  Addicted to Love (1997)  Adjustment Bureau, The (2011)  Adventureland (2009)  Adventures in Babysitting (1987)  Adventures of Baron Munchausen, The (1988)  Adventures of Buckaroo Banzai Across the 8th Dimension, The (1984)  Adventures of Milo and Otis, The (Koneko monogatari) (1986)  Adventures of Pinocchio, The (1996)  Adventures of Priscilla, Queen of the Desert, The (1994)  Adventures of Robin Hood, The (1938)  Adventures of Rocky and Bullwinkle, The (2000)  Adventures of Tintin, The (2011)  Aeon Flux (2005)  Affair to Remember, An (1957)  Affliction (1997)  African Queen, The (1951)  After Hours (1985)  Age of Innocence, The (1993)  Agnes of God (1985)  Aguirre: The Wrath of God (Aguirre, der Zorn Gottes) (1972)  Air America (1990)  Air Bud (1997)  Air Force One (1997)  Airheads (1994)  Airplane II: The Sequel (1982)  Airplane! (1980)  Airport (1970)  Akira (1988)  Aladdin (1992)  Aladdin and the King of Thieves (1996)  Alexander (2004)  Alfie (2004)  Ali (2001)  Alice in Wonderland (1951)  Alice in Wonderland (2010)  Alien (1979)  Alien Nation (1988)  Alien: Resurrection (1997)  Aliens (1986)  Alien³ (a.k.a. Alien 3) (1992)  Alive (1993)  All About Eve (1950)  All About My Mother (Todo sobre mi madre) (1999)  All Dogs Go to Heaven (1989)  All Dogs Go to Heaven 2 (1996)  All Quiet on the Western Front (1930)  All That Jazz (1979)  All the President's Men (1976)  All the Pretty Horses (2000)  Almost Famous (2000)  Along Came Polly (2004)  Along Came a Spider (2001)  Alphaville (Alphaville, une étrange aventure de Lemmy Caution) (1965)  Altered States (1980)  Always (1989)  Amadeus (1984)  Amateur (1994)  Amazing Spider-Man, The (2012)  Amelie (Fabuleux destin d'Amélie Poulain, Le) (2001)  America's Sweethearts (2001)  American Beauty (1999)  American Gangster (2007)  American Gigolo (1980)  American Graffiti (1973)  American History X (1998)  American Hustle (2013)  American Movie (1999)  American Pie (1999)  American Pie 2 (2001)  American President, The (1995)  American Psycho (2000)  American Splendo

### Step 3: Assign the movies rated by the selected user to a list named movies_watched.

In [8]:
movies_watched = random_user_df.columns[random_user_df.notna().any().tolist()]
movies_watched

Index(['10 Things I Hate About You (1999)', '2001: A Space Odyssey (1968)', 'African Queen, The (1951)', 'Annie Hall (1977)', 'Apollo 13 (1995)', 'Atlantic City (1980)', 'Austin Powers: International Man of Mystery (1997)', 'Austin Powers: The Spy Who Shagged Me (1999)', 'Babe (1995)', 'Beetlejuice (1988)', 'Big (1988)', 'Cape Fear (1962)', 'Casablanca (1942)', 'Cast Away (2000)', 'Crouching Tiger, Hidden Dragon (Wo hu cang long) (2000)', 'Emperor's New Groove, The (2000)', 'Frequency (2000)', 'Gods Must Be Crazy, The (1980)', 'Good Morning, Vietnam (1987)', 'Henry: Portrait of a Serial Killer (1986)', 'It's a Wonderful Life (1946)', 'Little Mermaid, The (1989)', 'Misery (1990)', 'Miss Congeniality (2000)', 'Monty Python and the Holy Grail (1975)', 'Naked Gun 33 1/3: The Final Insult (1994)', 'National Lampoon's Vacation (1983)', 'On Golden Pond (1981)', 'Patriot, The (2000)', 'Princess Bride, The (1987)', 'Return of Jafar, The (1994)', 'Shakespeare in Love (1998)',
       'Space Cowbo

---
# Task 3: Accessing the Data and Ids of Other Users Who Watched the Same Movies
---

### Step 1: Select the columns of the movies watched by the selected user from user_movie_df and create a new dataframe named movies_watched_df.

In [9]:
movies_watched_df = user_movie_df[movies_watched]
movies_watched_df.head()

title   10 Things I Hate About You (1999)  2001: A Space Odyssey (1968)  African Queen, The (1951)  Annie Hall (1977)  Apollo 13 (1995)  Atlantic City (1980)  Austin Powers: International Man of Mystery (1997)  Austin Powers: The Spy Who Shagged Me (1999)  Babe (1995)  Beetlejuice (1988)  Big (1988)  Cape Fear (1962)  Casablanca (1942)  Cast Away (2000)  Crouching Tiger, Hidden Dragon (Wo hu cang long) (2000)  Emperor's New Groove, The (2000)  Frequency (2000)  Gods Must Be Crazy, The (1980)  Good Morning, Vietnam (1987)  Henry: Portrait of a Serial Killer (1986)  It's a Wonderful Life (1946)  Little Mermaid, The (1989)  Misery (1990)  Miss Congeniality (2000)  Monty Python and the Holy Grail (1975)  Naked Gun 33 1/3: The Final Insult (1994)  National Lampoon's Vacation (1983)  On Golden Pond (1981)  Patriot, The (2000)  Princess Bride, The (1987)  Return of Jafar, The (1994)  Shakespeare in Love (1998)  Space Cowboys (2000)  Thirteen Days (2000)  Toy Story (1995)  Toy Story 2 (1999)  Wedding Planner, The (2001)  When Harry Met Sally... (1989)  Witness (1985)  Women on the Verge of a Nervous Breakdown (Mujeres al borde de un ataque de nervios) (1988)  World Is Not Enough, The (1999)  X-Files: Fight the Future, The (1998)  X-Men (2000)
userId                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                
1                                     NaN                           3.5                        NaN                NaN               NaN                   NaN                                                NaN                                            3.5          NaN                 4.0         NaN               NaN                NaN               NaN                                                4.0                                     NaN               NaN                             NaN                           NaN                                        NaN                           NaN                         NaN            4.0                       NaN                                     3.5                                        NaN                                 NaN                    NaN                  NaN                         NaN                          NaN                         NaN                   NaN                   NaN               NaN                 NaN                          NaN                             NaN             NaN                                                NaN                                                                        NaN                                    NaN           NaN
2                                     NaN                           5.0                        NaN                NaN               NaN                   NaN                                                NaN                           

### Step 2: Create a new dataframe named user_movie_count that carries the information of how many of the selected user's movies each user has watched.

In [10]:
user_movie_count = movies_watched_df.T.notnull().sum()
user_movie_count = user_movie_count.reset_index()
user_movie_count.columns = ["userId", "movie_count"]
user_movie_count.head()

userId  movie_count
0       1            6
1       2            2
2       3           10
3       4            1
4       5            3

### Step 3: Consider users who have watched 60% or more of the movies rated by the selected user as similar users.

In [11]:
perc = len(movies_watched) * 60 / 100
user_movie_count[user_movie_count["movie_count"] > perc].sort_values("movie_count", ascending=False)
user_movie_count[user_movie_count["movie_count"] == 33].count()
users_same_movies = user_movie_count[user_movie_count["movie_count"] > perc]["userId"]
users_same_movies.head()

userId  movie_count
83089    83090           43
28941    28942           43
71974    71975           42
8404      8405           42
118204  118205           42
...        ...          ...
114572  114573           26
31320    31321           26
31574    31575           26
114269  114270           26
38540    38541           26

[1764 rows x 2 columns]

userId         67
movie_count    67
dtype: int64

57      58
90      91
155    156
207    208
293    294
Name: userId, dtype: int64

---
# Task 4: Identifying the Most Similar Users to the User to be Recommended
---

### Step 1: Filter the movies_watched_df dataframe to include the ids of the users in the user_same_movies list.

In [12]:
final_df = movies_watched_df[movies_watched_df.index.isin(users_same_movies)]
final_df.shape

(1764, 43)

### Step 2: Create a new dataframe named corr_df containing the correlations of users with each other.

In [13]:
corr_df = final_df.T.corr().unstack().sort_values().drop_duplicates()
corr_df = pd.DataFrame(corr_df, columns=["corr"])
corr_df.index.names = ["user_id_1", "user_id_2"]
corr_df = corr_df.reset_index()
corr_df.head()

user_id_1  user_id_2      corr
0      30857      23317 -0.880865
1     100712      44882 -0.849849
2      73607      67387 -0.844208
3      39099      88228 -0.827848
4      17127     125178 -0.825732

### Step 3: Filter users with a high correlation (above 0.65) with the selected user and create a new dataframe named top_users.

In [14]:
top_users = corr_df[(corr_df["user_id_1"] == random_user) &
                    (corr_df["corr"] > 0.65)][["user_id_2", "corr"]].reset_index(drop=True)
top_users = top_users.sort_values(by="corr", ascending=False)
top_users.rename(columns={"user_id_2": "userId"}, inplace=True)
top_users.head()

userId      corr
1  122897  0.736153
0   46848  0.683185

### Step 4: Merge the top_users dataframe with the rating dataset.

In [15]:
top_users_ratings = top_users.merge(df_rating[["userId", "movieId", "rating"]], how="inner")
top_users_ratings = top_users_ratings[top_users_ratings["userId"] != random_user]
top_users_ratings.head()

userId      corr  movieId  rating
0  122897  0.736153        1     4.5
1  122897  0.736153        6     3.5
2  122897  0.736153        7     4.0
3  122897  0.736153       10     4.0
4  122897  0.736153       11     3.5

---
# Task 5: Calculating the Weighted Average Recommendation Score and Keeping the Top 5 Movies
---

### Step 1: Create a new variable named weighted_rating consisting of the product of each user's corr and rating values.

In [16]:
top_users_ratings["weighted_rating"] = top_users_ratings["corr"] * top_users_ratings["rating"]
top_users_ratings.groupby("movieId").agg({"weighted_rating": "mean"})

weighted_rating
movieId                 
1               3.193509
6               2.576534
7               2.944610
10              2.326286
11              2.576534
...                  ...
44199           2.944610
45186           2.944610
45431           2.576534
45501           2.944610
45517           2.944610

[1062 rows x 1 columns]

### Step 2: Create a new dataframe named recommendation_df containing the movie ids and the average weighted rating values for each movie.

In [17]:
recommendation_df = top_users_ratings.groupby("movieId").agg({"weighted_rating": "mean"})
recommendation_df = recommendation_df.reset_index()

### Step 3: Select the movies in the recommendation_df with a weighted rating greater than 3.5 and sort by weighted rating.

In [18]:
movies_to_be_recommend = recommendation_df[recommendation_df["weighted_rating"] > 3.5].sort_values(by="weighted_rating", ascending=False)
movies_to_be_recommend.head()

movieId  weighted_rating
19       110         3.680763
806     5064         3.680763
486     2928         3.680763
496     2984         3.680763
597     3578         3.680763

### Step 4: Retrieve the names of the top 5 recommended movies.

In [19]:
movies_to_be_recommend.merge(df_movie[["movieId", "title"]]).head(5)

movieId  weighted_rating                             title
0      110         3.680763                 Braveheart (1995)
1     5064         3.680763  The Count of Monte Cristo (2002)
2     2928         3.680763          Razor's Edge, The (1984)
3     2984         3.680763              On Any Sunday (1971)
4     3578         3.680763                  Gladiator (2000)